# Пайплайн № 6
### База знаний: FAQ, Реальные Кейсы, Пользовательское соглашение и Условия размещения

### Защита от галлюцинаций: если не уверены в ответе - возвращаем "Нет ответа", но отдаём два классификатора.

### Добавили Ranker, который более тщательно ранжирует релевантные вопросы

### Установка необходимых библиотек

In [64]:
%%bash

pip install haystack-ai
pip install "datasets>=2.6.1"
pip install "sentence-transformers>=3.0.0"
pip install pymorphy2
pip install catboost
pip install python-docx

### Подготовка данных

In [65]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [66]:
!cp -r drive/MyDrive/HacksAI/Russia24/Dataset Dataset/

Эталонная База Знаний FAQ

In [67]:
import pandas as pd
import json

know_base_path = 'Dataset/01_База_знаний.xlsx'
df_base = pd.read_excel(know_base_path)

df_base.head()

Тема  \
0                   Что нельзя публиковать на RUTUBE   
1  Почему могут отключить монетизацию на видео и ...   
2  Почему могут отключить монетизацию на видео и ...   
3  Почему могут отключить монетизацию на видео и ...   
4                                    Авторское право   

                                        Вопрос из БЗ  \
0                  Что нельзя публиковать на RUTUBE?   
1  Почему могут отключить монетизацию из-за автор...   
2  Почему могут отключить монетизацию из-за искус...   
3  Для каких статусов доступна монетизация, и поч...   
4  Какой контент можно использовать для монетизац...   

                                         Ответ из БЗ Классификатор 1 уровня  \
0  Чужой контент без разрешения автора или правоо...              МОДЕРАЦИЯ   
1  Монетизация может отключиться, если на вашем к...            МОНЕТИЗАЦИЯ   
2  Монетизация на RUTUBE зависит в том числе от к...            МОНЕТИЗАЦИЯ   
3  Монетизацию на RUTUBE можно подключить, если в...            МОНЕТИЗАЦИЯ   
4  То, что вы создали сами: видео, которое вы сня...            МОНЕТИЗАЦИЯ   

               Классификатор 2 уровня  
0         Отклонение/блокировка видео  
1  Отключение/подключение монетизации  
2  Отключение/подключение монетизации  
3  Отключение/подключение монетизации  
4  Отключение/подключение монетизации

База Реальных Кейсов

In [68]:
real_case_path = 'Dataset/02_Реальные_кейсы.xlsx'
df_case = pd.read_excel(real_case_path)

df_case.head()

Вопрос пользователя  \
0  Здравствуйте! Можно уточнить причины Правилhtt...   
1  Добрый вечер, какой топ причин блокировки виде...   
2  Все пишут, что монетизация на рутубе отключает...   
3  Что запрещено в монетизации и что можно выклад...   
4  Чтобы не отключали монетизацию, надо, чтобы я ...   

                                    Ответ сотрудника  \
0  Добрый день!\nЧто нельзя публиковать на RUTUBE...   
1  Добрый вечер!\nЧто заперщено публиковать на RU...   
2  Добрый день! \nМонетизация может отключиться, ...   
3  Здравствуйте!\nМонетизация может отключиться, ...   
4  Для монетизации можно использовать то, что вы ...   

                                        Вопрос из БЗ  \
0                  Что нельзя публиковать на RUTUBE?   
1                  Что нельзя публиковать на RUTUBE?   
2  Почему могут отключить монетизацию из-за автор...   
3  Почему могут отключить монетизацию из-за автор...   
4  Почему могут отключить монетизацию из-за автор...   

                                         Ответ из БЗ Классификатор 1 уровня  \
0  Чужой контент без разрешения автора или правоо...              МОДЕРАЦИЯ   
1  Чужой контент без разрешения автора или правоо...              МОДЕРАЦИЯ   
2  Монетизация может отключиться, если на вашем к...            МОНЕТИЗАЦИЯ   
3  Монетизация может отключиться, если на вашем к...            МОНЕТИЗАЦИЯ   
4  Монетизация может отключиться, если на вашем к...            МОНЕТИЗАЦИЯ   

               Классификатор 2 уровня  
0         Отклонение/блокировка видео  
1         Отклонение/блокировка видео  
2  Отключение/подключение монетизации  
3  Отключение/подключение монетизации  
4  Отключение/подключение монетизации

Объединим обе базы для полее полного и объективного поиска

In [69]:
combined_column = pd.concat([df_base['Вопрос из БЗ'], df_case['Вопрос пользователя']], ignore_index=True)

df_base_rest = df_base.drop(columns=['Вопрос из БЗ'])
df_case_rest = df_case.drop(columns=['Вопрос пользователя'])

combined_rest = pd.concat([df_base_rest, df_case_rest], ignore_index=True)

final_df = combined_rest.copy()
final_df['Вопрос'] = combined_column

final_df = final_df[['Вопрос'] + [col for col in final_df.columns if col != 'Вопрос']]
final_df = final_df.drop(columns=["Тема"])

final_df.tail()

Вопрос  \
1122  Добрый день! Как добавить таймкоды в видео?   
1123             Как добавить временные интервалы   
1124        В каком формате добавляются таймкоды?   
1125          Как мне правильно указать тайм-код?   
1126     Как правильно указывать время под видео?   

                                            Ответ из БЗ  \
1122  Перейдите в раздел «Видео» в Студии RUTUBE.\nН...   
1123  Перейдите в раздел «Видео» в Студии RUTUBE.\nН...   
1124  Главное — соблюдать несколько правил.\n\nТайм-...   
1125  Главное — соблюдать несколько правил.\n\nТайм-...   
1126  Главное — соблюдать несколько правил.\n\nТайм-...   

     Классификатор 1 уровня Классификатор 2 уровня  \
1122                  ВИДЕО         Загрузка видео   
1123                  ВИДЕО         Загрузка видео   
1124                  ВИДЕО         Загрузка видео   
1125                  ВИДЕО         Загрузка видео   
1126                  ВИДЕО         Загрузка видео   

                                       Ответ сотрудника  \
1122  Характеристики эпизодов:\n\nОпределяются по та...   
1123  Перейдите в раздел «Видео» в Студии RUTUBE.\nН...   
1124  Формат: минуты:секунды или часы:минуты:секунды...   
1125  Можете указать минуты:секунды или часы:минуты:...   
1126  Тайм-код должен отображать время в формате мин...   

                                           Вопрос из БЗ  
1122                  Как добавить тайм-коды под видео?  
1123                  Как добавить тайм-коды под видео?  
1124  В каком формате нужно добавлять тайм-коды под ...  
1125  В каком формате нужно добавлять тайм-коды под ...  
1126  В каком формате нужно добавлять тайм-коды под ...

In [70]:
import docx
from haystack import Document

docs = [Document(content=row["Вопрос"], meta={"source": "Общая база вопросов", "idx": index}) for index, row in final_df.iterrows()]

Добавим документы: Пользовательское соглашение и Условия размещения

In [71]:
my_doc = docx.Document('Dataset/03_ГЕНЕРАЛЬНОЕ_ПОЛЬЗОВАТЕЛЬСКОЕ_СОГЛАШЕНИЕ_RUTUBE.docx')
para_list = [paragraph.text for paragraph in my_doc.paragraphs if paragraph.text != ""]

para_tuples_list = []

for paragraph in para_list:
    parts = paragraph.split("    ")
    if len(parts) > 1:
        point, content = parts[0].strip(), parts[-1].strip()
        # Разбиваем содержание на чанки по 500 символов
        for i in range(0, len(content), 2048):
            chunk = content[i:i+2048]
            para_tuples_list.append((point, chunk))


for index, paragraph in para_tuples_list:
  docs.append(Document(content=paragraph, meta={"source": "Генеральное пользовательское соглашение", "idx": index}))

In [72]:
para_tuples_list

[('1.', 'ПРЕАМБУЛА.'),
 ('1.1.',
  'Настоящее Пользовательское соглашение, именуемое в дальнейшем «Соглашение», представляет собой публичную оферту в адрес любого совершеннолетнего физического лица, прошедшего Процедуру регистрации/ авторизацию в RUTUBE в порядке предусмотренном, Соглашением, и использующим какие-либо из предоставленных возможностей RUTUBE от Общества с ограниченной ответственностью «РУФОРМ» (ИНН 7714886605, ОГРН 1127747031840), зарегистрированного по адресу: 101000, г. Москва, ул. Мясницкая, д.46, стр. 7, офис I, комн. 16, именуемого в дальнейшем «Администрация», являющегося Стороной первого российского Меморандума о сотрудничестве в сфере охраны исключительных прав в эпоху развития цифровых технологий от «01» ноября 2018 года (далее по тексту – Меморандум), а также лицом, на законных основаниях управляющим RUTUBE и предоставляющим неограниченному кругу лиц (Пользователям/ Авторам и/или по отдельным письменным соглашениям - Правообладателям) возможность посредством се

In [73]:
my_doc = docx.Document('Dataset/04_УСЛОВИЯ РАЗМЕЩЕНИЯ КОНТЕНТА.docx')
para_list = [paragraph.text for paragraph in my_doc.paragraphs if paragraph.text != ""]

para_tuples_list = []

for paragraph in para_list:
    parts = paragraph.split(".")
    idx = parts[0].strip() if len(parts[0].strip()) <= 2 else ""
    content = ".".join(parts[1:]).strip() if idx else paragraph.strip()

    # Разбиваем содержание на чанки
    for i in range(0, len(content), 2048):
        chunk = content[i:i+2048]
        para_tuples_list.append((idx, chunk))

for index, paragraph in para_tuples_list:
  docs.append(Document(content=paragraph, meta={"source": "Условия размещение контента", "idx": index}))

In [74]:
len(docs)

1322

### Инициализируем Трансформер для построения эмбеддинга вопросов

In [75]:
from haystack.components.embedders import SentenceTransformersDocumentEmbedder
from haystack.utils import ComponentDevice, Device

device = ComponentDevice.from_str("cuda:0")

# embed_model = "cointegrated/LaBSE-en-ru"
embed_model = "intfloat/e5-large-v2"

doc_embedder = SentenceTransformersDocumentEmbedder(
    model=embed_model,
    device=device
    )

doc_embedder.warm_up()

### Запишем вопросы в векторное хранилище

In [76]:
from haystack.document_stores.in_memory import InMemoryDocumentStore

document_store = InMemoryDocumentStore()

docs_with_embeddings = doc_embedder.run(docs)
unique_docs = {doc.id: doc for doc in docs_with_embeddings["documents"]}.values()
document_store.write_documents(list(unique_docs))

Batches:   0%|          | 0/42 [00:00<?, ?it/s]

1322

### Инициализируем Трансформер для поиска по эмбеддингам вопросов
он должен совпадать с трансформером, на основе которого строились эмбеддинги

In [77]:
from haystack.components.embedders import SentenceTransformersTextEmbedder

text_embedder = SentenceTransformersTextEmbedder(
    model=embed_model,
    device=device
)

### Инициализируем Retriever

In [78]:
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever

retriever = InMemoryEmbeddingRetriever(document_store, top_k=100)

## Собираем пайплайн

In [79]:
from haystack import Pipeline

from haystack.components.rankers import TransformersSimilarityRanker

ranker = TransformersSimilarityRanker(
    model="DiTy/cross-encoder-russian-msmarco",
    top_k=1
    )

basic_rag_pipeline = Pipeline()
# Add components to your pipeline
basic_rag_pipeline.add_component("text_embedder", text_embedder)
basic_rag_pipeline.add_component("retriever", retriever)
basic_rag_pipeline.add_component("ranker", ranker)

# Now, connect the components to each other
basic_rag_pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
basic_rag_pipeline.connect("retriever", "ranker")

🚅 Components
  - text_embedder: SentenceTransformersTextEmbedder
  - retriever: InMemoryEmbeddingRetriever
  - ranker: TransformersSimilarityRanker
🛤️ Connections
  - text_embedder.embedding -> retriever.query_embedding (List[float])
  - retriever.documents -> ranker.documents (List[Document])

In [80]:
question = 'Администрация'

basic_rag_pipeline.run({"text_embedder": {"text": question}, "ranker":{"query": question}})

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


{'ranker': {'documents': [Document(id=d433d94d4c2a46cd57da7ae0ddab7e73bc956e1bf51ba7a4303b6ef266ed2535, content: 'ПРЕАМБУЛА.', meta: {'source': 'Генеральное пользовательское соглашение', 'idx': '1.'}, score: 0.33653345704078674)]}}

Добавим словарь, по которому будем заменять англицизмы на действительно английские слова (т. к. в базе они хранятся именно на английском)

In [81]:
replace_dict = {
    'шортс': 'shorts',
    "рутуб": "rutube",
    "рутубе": "rutube",
    "рутуба": "rutube",
    "рутубу": "rutube",
    "ютуб": "youtube",
    "ютубе": "youtube",
    "ютуба": "youtube",
    "ютубу": "youtube",
    "смарт": "smart",
    "тв": "tv",
    "самсунг": "samsung",
    "урл": "url",
}

### Загрузим предварительно обученные модели для будущей классификации вопросов

In [82]:
!cp -r drive/MyDrive/HacksAI/Russia24/models/version_20240928_121531_train_0.80_test_0.66_valid_0.61/ model_1/
!cp -r drive/MyDrive/HacksAI/Russia24/models/version_20240928_123836_train_0.45_test_0.41_valid_0.32/ model_2/

Вспомогательные функции для моделей классификации

In [83]:
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
import joblib

nltk.download('punkt')
nltk.download('wordnet')
nltk.download('stopwords')

lemmatizer = WordNetLemmatizer()
stop_words = set(stopwords.words('russian'))

loaded_models = {}
loaded_encoders = {}
loaded_vectorizers = {}

def preprocess(text):
    text = re.sub(r'\W+', ' ', text)

    words = nltk.word_tokenize(text)
    words = [lemmatizer.lemmatize(word) for word in words if word not in stop_words]

    return ' '.join(words)

def load_model_and_files(model_name, model_path, encoder_path, vectorizer_path):
    global loaded_models, loaded_encoders, loaded_vectorizers

    if model_name not in loaded_models:
        print(f"Загрузка модели {model_name}...")
        loaded_models[model_name] = joblib.load(model_path)
        loaded_encoders[model_name] = joblib.load(encoder_path)
        loaded_vectorizers[model_name] = joblib.load(vectorizer_path)
    else:
        print(f"Модель {model_name} уже загружена.")

def classify_question(
    question: str,
    model_name: str,
):
    global loaded_models, loaded_encoders, loaded_vectorizers

    preprocessed_question = preprocess(question)

    # Преобразование вопроса в TF-IDF вектор
    vectorizer = loaded_vectorizers[model_name]
    question_tfidf = vectorizer.transform([preprocessed_question])

    # Предсказание с помощью модели
    model = loaded_models[model_name]
    predicted_label_numeric = model.predict(question_tfidf)

    # Преобразование числовой метки обратно в текстовую метку
    encoder = loaded_encoders[model_name]
    predicted_label_text = encoder.inverse_transform(predicted_label_numeric)

    return predicted_label_text[0]

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [84]:
model_path_1 = "model_1/classifier_1.pkl"
encoder_path_1 = "model_1/label_encoder_1.pkl"
vectorizer_path_1 = "model_1/vectorizer_1.pkl"

model_path_2 = "model_2/classifier_2.pkl"
encoder_path_2 = "model_2/label_encoder_2.pkl"
vectorizer_path_2 = "model_2/vectorizer_2.pkl"

load_model_and_files('model_1', model_path_1, encoder_path_1, vectorizer_path_1)
load_model_and_files('model_2', model_path_2, encoder_path_2, vectorizer_path_2)

Загрузка модели model_1...
Загрузка модели model_2...


### Интерфейс для получения ответа из RAG пайплайна

In [85]:
import pymorphy2

morph = pymorphy2.MorphAnalyzer()

def preprocess_text(text):
    """
    Функция предобработки текста: приведение к нижнему регистру, удаление лишних символов,
    лемматизация и замена слов по словарю, с сохранением знаков препинания.
    Если слово не найдено в replace_dict, оно остаётся в исходной форме.
    """
    # Токенизация: разделяем слова и знаки препинания
    tokens = re.findall(r'\w+|[^\w\s]', text.lower())
    processed_tokens = []

    for token in tokens:
        if re.match(r'\w+', token):  # Если это слово
            if replace_dict and token in replace_dict:
                # Заменяем слово, если оно есть в словаре
                processed_tokens.append(replace_dict[token])
            else:
                # Если нет в словаре замен, оставляем слово как есть
                processed_tokens.append(token)
        else:
            # Знак препинания остаётся без изменений
            processed_tokens.append(token)

    # Восстановление текста с правильным расположением знаков препинания
    processed_text = ''
    for i, token in enumerate(processed_tokens):
        if token in '.,!?;:':
            # Прикрепляем знак препинания к предыдущему слову без пробела
            processed_text = processed_text.rstrip() + token + ' '
        else:
            processed_text += token + ' '

    return processed_text.strip()

In [86]:
import re
import time
import pandas as pd

def get_answer_from_rag(
    question: str,
    basic_rag_pipeline,
    threshold: float = 0.35,
    df:pd.DataFrame = final_df,
    ):
    start_time = time.time()

    question = preprocess_text(question)
    # print(f"Вопрос после очистки: {question}")

    response = basic_rag_pipeline.run({"text_embedder": {"text": question}, "ranker": {"query": question}})
    # print(response)

    document = response['ranker']['documents'][0]

    target_q = document.content
    score = document.score

    if score  < threshold:
      answer_text = "Ответ не найден."
      class_1 = classify_question(question, "model_1")
      class_2 = classify_question(question, "model_2")
    elif document.meta['source'] in ("Генеральное пользовательское соглашение", "Условия размещение контента"):
      answer_text = f"{document.content}\nИсточник: {document.meta['source']} {document.meta['idx']}" # TODO
      class_1 = classify_question(question, "model_1")
      class_2 = classify_question(question, "model_2")
    else:
      target_answer = df.loc[df['Вопрос'] == target_q].iloc[0]

      answer_text = target_answer['Ответ из БЗ']
      class_1 = target_answer['Классификатор 1 уровня']
      class_2 = target_answer['Классификатор 2 уровня']

    print("Затраченное время:", time.time() - start_time)

    return answer_text, class_1, class_2

In [87]:
get_answer_from_rag(
    "Администрация вправе",
    basic_rag_pipeline,
    threshold = 0.5)

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Затраченное время: 3.2722580432891846


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


('Администрация вправе осуществлять замену либо удаление слов и выражений, сопровождающих Информацию и Контент, размещенных Пользователем и которые можно счесть оскорбительными либо нарушающими права третьих лиц или нарушающими нормы действующего законодательства Российской Федерации.\nИсточник: Генеральное пользовательское соглашение 5.2.',
 'УПРАВЛЕНИЕ АККАУНТОМ',
 'Персонализация')

In [88]:
get_answer_from_rag(
    "Умпа лумпа",
    basic_rag_pipeline)

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Затраченное время: 0.9277386665344238


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


('Ответ не найден.', 'УПРАВЛЕНИЕ АККАУНТОМ', 'Персонализация')

### Асинхронная функция для будущего использования с API

In [89]:
import asyncio
from pydantic import BaseModel

class Answer(BaseModel):
    answer: str
    class_1: str
    class_2: str
    # source_type: str # "FAQ", "Agreement", "Content"
    # source_text: str

async def get_answer(question: str, basic_rag_pipeline) -> Answer:
    """
    Асинхронная функция принимает вопрос, получает ответ и классы с помощью RAG pipeline
    и возвращает объект AnswerModel.

    Параметры:
    - question (str): Вопрос, который нужно обработать.
    - basic_rag_pipeline: RAG pipeline для обработки запроса.
    - replace_dict (dict, optional): Словарь для замены слов в вопросе.
    - df (pd.DataFrame, optional): DataFrame, содержащий столбцы 'Вопрос из БЗ', 'Ответ из БЗ',
                                    'Классификатор 1 уровня' и 'Классификатор 2 уровня'.

    Возвращает:
    - AnswerModel: Объект с полями answer, class_1 и class_2.
    """
    loop = asyncio.get_event_loop()
    answer_text, class_1, class_2 = await loop.run_in_executor(
        None,
        get_answer_from_rag,
        question,
        basic_rag_pipeline,
    )

    return Answer(
        answer=answer_text,
        class_1=class_1 if class_1 else "",
        class_2=class_2 if class_2 else "",
    )

In [90]:
ttest = await get_answer("Умпа Лумпа?", basic_rag_pipeline)
print("-------------")
print(ttest)

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Затраченное время: 0.709611177444458
-------------
answer='Ответ не найден.' class_1='УПРАВЛЕНИЕ АККАУНТОМ' class_2='Персонализация'


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


### Тест модели

In [91]:
import pandas as pd

def process_all_questions(input_file, question_col, basic_rag_pipeline, output_file):
    """
    Функция обрабатывает все вопросы из указанного файла, вызывает get_answer_from_rag для каждого,
    и сохраняет результаты в новый CSV файл.

    Параметры:
    - input_file: Путь к CSV или XLSX файлу с вопросами.
    - question_col: Название колонки, содержащей вопросы.
    - basic_rag_pipeline: RAG pipeline для обработки запроса.
    - output_file: Путь для сохранения результирующего CSV файла с вопросами и ответами.

    Возвращает:
    - DataFrame с исходными вопросами и найденными ответами.
    """

    file_extension = input_file.split('.')[-1].lower()

    # Чтение данных в зависимости от расширения
    if file_extension == 'csv':
        df_questions = pd.read_csv(input_file)
    elif file_extension == 'xlsx':
        df_questions = pd.read_excel(input_file)
    else:
        raise ValueError("Файл должен быть формата CSV или XLSX.")

    results = []

    for question in df_questions[question_col]:
        answer, сlass_1, class_2 = get_answer_from_rag(question, basic_rag_pipeline)
        results.append({'Вопрос': question, 'Ответ': answer})

    df_results = pd.DataFrame(results)
    df_results.to_csv(output_file, index=False, encoding='utf-8')

    print(f"Результаты сохранены в файл: {output_file}")
    return df_results

In [92]:
main_path = "drive/MyDrive/HacksAI/Russia24/"

src_file_path = main_path + "ground_truth_data/gt_faq_and_cases_evaluation.xlsx"
out_file_path = main_path + "generated_data/pipeline6_answers.csv"

process_all_questions(src_file_path, 'Вопрос', basic_rag_pipeline, out_file_path)

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Затраченное время: 0.46669936180114746


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Затраченное время: 0.5562448501586914


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


...

Затраченное время: 0.7382853031158447


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Затраченное время: 0.7615172863006592
Результаты сохранены в файл: drive/MyDrive/HacksAI/Russia24/generated_data/pipeline6_answers.csv


Вопрос  \
0                  Что запрещено выкладывать на RUTUBE?   
1     Какого черта могут вырубить рекламу из-за авто...   
2     Почему могут приостановить заработок из-за нак...   
3     На какие статусы можно заработать деньги и поч...   
4     Какой контент можно юзать, чтобы заработать де...   
...                                                 ...   
1122       Как я могу вставить временные метки в видео?   
1123           Как мне прикрепить временные промежутки?   
1124   Какой формат использовать для вставки таймкодов?   
1125                   Как мне поставить время в точку?   
1126     Как я могу поставить время на видео правильно?   

                                                  Ответ  
0     Чужой контент без разрешения автора или правоо...  
1                                      Ответ не найден.  
2     Монетизация на RUTUBE зависит в том числе от к...  
3     Монетизацию на RUTUBE можно подключить, если в...  
4     То, что вы создали сами: видео, которое вы сня...  
...                                                 ...  
1122  Перейдите в раздел «Видео» в Студии RUTUBE.\nН...  
1123  Перейдите в раздел «Видео» в Студии RUTUBE.\nН...  
1124  Главное — соблюдать несколько правил.\n\nТайм-...  
1125                                   Ответ не найден.  
1126  Главное — соблюдать несколько правил.\n\nТайм-...  

[1127 rows x 2 columns]